# Final Project

In [1]:
import pandas as pd
import numpy as np
from numpy.random import rand
from landscape import Landscape # Import methods from inside file landscape.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm
import matplotlib.colors
import matplotlib as mpl
%matplotlib qt

## Landscape Features

### Elevation Modifiers

In [140]:
# Some Randomness
def initial_conditions(NX,NY):
    Z = rand(NX,NY)
    return Z

# Primary Geologic Features Features
def AddHill(Z,NX,NY,xx,yy,r,h):

    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2;
            dr = np.sqrt(dx**2+dy**2);
            if (dr<r):
                Z[x,y] += h * (np.cos(dr/r*np.pi/2.0))**2;

    return Z

 

### Feature Modifiers

In [141]:
# Vegetation: Landslide/Erosion Mitigation
def AddRandVegetation(NX,NY):
    randveg = np.array(rand(NX,NY)+0.5).astype(int)+1
    return randveg

def AddForest(veg,NX,NY,xx,yy,r):
    
    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2;
            dr = np.sqrt(dx**2+dy**2);
            if (dr<r):
                veg[x,y] = int(4*(r-dr)/r)+1;
    
    return veg
    
# Soil Type: Landslide/Erosion factor
def AddSoilType(NX,NY):
    soil = np.array(rand(NX,NY)*0).astype(int)
    
    for i in np.arange(1,6):
        soilx = int(rand()*NX)
        soily = int(rand()*NY)
        soil[soilx,soily] = i

    newsoil = np.copy(soil)
    while np.any(soil==0):
        for x in np.arange(NX):
            xU = (x+1)%NX
            xD = (x-1)%NX
            for y in np.arange(NY):
                yU = (y+1)%NY
                yD = (y-1)%NY
                adjacent = np.array([soil[xU,yU],soil[xU,y],soil[xU,yD],soil[x,yU],\
                                   soil[x,yD],soil[xD,yU],soil[xD,y],soil[xD,yD]])
                if np.any(adjacent!=0):
                    num1s = np.sum(adjacent==1)
                    num2s = np.sum(adjacent==2)
                    num3s = np.sum(adjacent==3)
                    num4s = np.sum(adjacent==4)
                    num5s = np.sum(adjacent==5)
                    nearby = np.array([num1s,num2s,num3s,num4s,num5s])
                    nearbymax = np.max(nearby)
                    nearbys = np.arange(np.sum(nearby==nearbymax))
                    newsoil[x,y] = np.argwhere(nearby==nearbymax)[np.random.choice(nearbys)][0]+1
        soil = np.copy(newsoil)
    
    return soil           

### Update Functions

In [142]:
def UpdateSoilVegetation(veg,soil,NX,NY):
    
    for x in range(NX):
        for y in range(NY):
            random_v = np.random.random()
            random_s = np.random.random()
            p_deg_v = 0.005*soil[x,y]
            p_imp_v = 0.005*(6-soil[x,y])
            p_imp_s = 0.0001*veg[x,y]
            if random_v < p_deg_v:
                if veg[x,y] != 1:
                    veg[x,y] -= 1
                else:
                    continue
            elif random_v > (1-p_imp_v):
                if veg[x,y] != 4:
                    veg[x,y] += 1
                else:
                    continue
            else:
                continue
            
            if random_s < p_imp_s:
                if soil[x,y] != 1:
                    soil[x,y] -= 1
                else:
                    continue
            else:
                continue
    
    return veg,soil

def UpdateGradientMap(gradient_map,gradient,x,y):
    gradient_map[x,y] = gradient
    return gradient_map

In [171]:
def find_river(Z):
    river = Z<(np.min(Z)+np.mean(Z)-1.25*np.std(Z))
    return river

def dist_river(X,Y,NX,NY,river):
    dimensions = np.array([NX,NY])
    positions = np.vstack([X.ravel(), Y.ravel()])
    distances = np.zeros(river.shape)
    river = 100000*(1-river)+1
    local_dists = []
    for i in np.arange(len(positions[0])):
        x0 = positions[:,i]
        for j in np.arange(len(positions[0])):
            x1 = positions[:,j]
            dist = distance(x0,x1,dimensions)
            if dist == 0:
                dist = 10000
            local_dists.append(dist)
        reshaped_dists = np.reshape(np.array([local_dists]),river.shape)
        valid_dists = np.min(river*reshaped_dists)
        distances[x0[0],x0[1]] = np.min(valid_dists)
        local_dists = []
    
    return (distances-1)/np.max(distances)
            
    
def distance(x0, x1, dimensions):
    delta = np.abs(x0 - x1)
    delta = np.where(delta > 0.5 * dimensions, delta - dimensions, delta)
    return np.sqrt((delta ** 2).sum(axis=-1))

### Create Landslide Map

In [161]:
def LandslideMap(river,gradient,veg,soil,river_dist):
    # Make Gradient Map Ratings with max of 10
    gradient = 10*gradient
    
    river_dist = 5*(1-river_dist)
    
    local_probs = (1-river)*(gradient+river_dist+soil-veg)
    
    return local_probs

### Figure Updating

In [168]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,12.))
    plt.show()
    return fig

def to_color(values,vmin,vmax,colormap):
    norm = mpl.colors.Normalize(vmin=vmin, vmax=vmax)
    cmap = colormap
    m = cm.ScalarMappable(norm=norm, cmap=cmap)
    return m.to_rgba(values),m


def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(321,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,np.max(Z) *1.5)

        ax1.set_title('Surface Relief x '+str(vert_exag))

        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(322,aspect='equal')
        ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        im = ax2.pcolor(Z,cmap=cm.coolwarm)
        cs = ax2.contour(Z,6,colors='k')

        # Add a color bar which maps values to colors.
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        cbar.add_lines(cs)
        
        ax3 = fig.add_subplot(323,projection='3d')
        ax3.set_title('Landslide Risk')
        
        ax3.set_xlim3d(0,max(NX,NY))
        ax3.set_ylim3d(0,max(NX,NY))
        ax3.set_zlim3d(0,np.max(Z)*1.5)
        
        values = LandslideMap(river,gradient_map/gradientmax,veg_map,soil_map,river_dist)
        colors,im = to_color(values,-4,17,cm.YlOrRd)
        
        surf = ax3.plot_surface(X,Y,Z, rstride=1, cstride=1, facecolors = colors,
                antialiased=False,linewidth=0)
        
        
        fig.colorbar(im, ax = ax3,shrink=0.5, aspect=5)
        
        ax4 = fig.add_subplot(324,projection='3d')
        ax4.set_title('Vegetation')
        
        ax4.set_xlim3d(0,max(NX,NY))
        ax4.set_ylim3d(0,max(NX,NY))
        ax4.set_zlim3d(0,np.max(Z)*1.5)
        
        values = veg_map
        colors,im = to_color(values,1,5,cm.Greens)
        
        surf = ax4.plot_surface(X,Y,Z, rstride=1, cstride=1, facecolors = colors,
                antialiased=False,linewidth=0)
        
        fig.colorbar(im, ax = ax4, shrink=0.5, aspect=5)
        
        ax5 = fig.add_subplot(325,aspect = 'equal')
        im = ax5.imshow(soil_map,origin='lower',cmap = 'YlOrBr_r')
        fig.colorbar(im, ax=ax5,shrink=0.5, aspect=5)
        
        ax6 = fig.add_subplot(326,aspect = 'equal')
        ax6.set_title('Distance to Water')
        
        im = ax6.imshow(river_dist,origin='lower',cmap = 'Blues_r')
        
        fig.colorbar(im, ax = ax6, shrink=0.5, aspect=5)
        
        #plt.show()
        plt.draw()
        plt.pause(0.05)

## Setting Up Simulation

### Initial Conditions

In [199]:
NX = 70 #number of rows
NY = 70 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

Z = initial_conditions(NX,NY)

x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) #strange that y goes first !!!

### Simulation Constants

In [170]:
### Physical Parameters
K = 1.0e-6 # meters^(1-2m)/yr

D = 0.005 # m^2/yr

# uplift rate
uplift = 0.003 / 600.

### Model parameters

# Set the time step dt
# Remember for 2D diffusion problems we need eta = D * dt / dx^2 < 1/4
# but because of the fluvial erosion terms please use eta < 1/8 or less
dt = (dx**2)/(16*D)
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=1.1

#gradient exponent g^n, default n=1
n=1.1

#erosion threshold 
theta_c = 20 

# Total simulation time
T = 2000.0 * 625.0

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of interations: ',n_iter)



 dt[years] =  312.5
Number of interations:  4000


### Initialize Landscape

In [200]:
# Initialize landscape 
for i in range(5):
    xx = rand()*NX
    yy = rand()*NY
    r  = (0.1+rand())*NX
    h  = (0.1+rand())*5
    Z = AddHill(Z,NX,NY,xx,yy,r,h)

for i in range(3):
    xx = rand()*NX
    yy = rand()*NY
    r  = (0.1+rand())*NX/2
    h  = (0.5+rand())*20
    Z = AddHill(Z,NX,NY,xx,yy,r,h)
      
ls = Landscape(NX,NY)
ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))
veg_map = AddRandVegetation(NX,NY)
veg_map = AddForest(veg_map,NX,NY,rand()*NX,rand()*NY,(0.5+rand())*NX/2)
soil_map = AddSoilType(NX,NY)
gradient_map = np.zeros(Z.shape)
river = find_river(Z)
river_dist = dist_river(X,Y,NX,NY,river)
veg_map = veg_map*(1-river)

## Run Simulation

In [177]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Landslide Susceptibility', artist='Matplotlib',comment='New Parameters')
writer = FFMpegWriter(fps=5, metadata=metadata,bitrate=20000)

In [178]:
fig = init_figure()
Znew = np.copy(Z)
gradientmax=0
with writer.saving(fig, "animation8.mp4", dpi=200):
    update_figure()
    writer.grab_frame()
    for it in range(1,2000+1):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A = ls.A*(dx*dy)

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.drain[i,j]>0: #this cell is a drain
                    s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                    s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                    s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                    s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                    gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.

                    # Update Gradient Map
                    gradient_map = UpdateGradientMap(gradient_map,gradient,i,j)
                    if gradient>gradientmax:
                        gradientmax=gradient
                
                    Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                    if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                        gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                    elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                        gradient = (Z[i,j]-Z[iL,j])/dx
                    elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                        gradient = (Z[i,j]-Z[i,jU])/dy
                    elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                        gradient = (Z[i,j]-Z[i,jD])/dy
                    else:
                        gradient = 0.02 # ??? This does happen (maybe when two pools merge

                    # Update Gradient Map
                    gradient_map = UpdateGradientMap(gradient_map,gradient,i,j)

                    Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                    Psi_z = 0.

                if (Psi_z<0):
                    Psi_z = 0. 

                # diffusion term, derive in terms of D,Z[:,:],dx,dy
                Phi_z = D*((Z[iL,j]-2*Z[i,j]+Z[iR,j])/dx**2+(Z[i,jU]-2*Z[i,j]+Z[i,jD])/dy**2)
                if river[i,j]==1:
                    Phi_z=0
                    Psi_z=0
                    uplift=0
                # insert Phi_z, Psi_z, and uplift terms to obtain new elevation Znew[i,j]
                Znew[i,j] = Z[i,j] + (Phi_z+Psi_z+uplift)*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        veg_map,soil_map = UpdateSoilVegetation(veg_map,soil_map,NX,NY)
        veg_map = veg_map*(1-river)
        # Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,10)==0): 
            print(it,end='')
            update_figure()
            writer.grab_frame()
        else:
            print('.',end='')

update_figure()
print(' Simulation finished.')

C:\Users\conno\Anaconda3\lib\site-packages\ipykernel_launcher.py:48: RuntimeWarning: invalid value encountered in true_divide


.........10.........20.........30.........40.........50.........60.........70.........80.........90.........100.........110.........120.........130.........140.........150.........160.........170.........180.........190.........200.........210.........220.........230.........240.........250.........260.........270.........280.........290.........300.........310.........320.........330.........340.........350.........360.........370.........380.........390.........400.
.
.......410.........420.........430.........440.........
450.........460.........470.........480.........490.
...
..
...500..
.......510........
.520.........530.........540.........550...
......560.........570.........
580.........590
.........600.........610.........620.........630.....
....640.........650.........660
.........670..
....
...
680...

...
.
..690.........700........

.710.........720.........730......
...740.........750...
....
.
.760..
....
...770
....
...
..780......
...790...
......
800
....
.....810.

...
.960.......
.
.

970
.........980..

.
.
...
.
.990...
.
...
..1000...
....
..1010.
.
..
..
..
.1020.

......
..1030.........1040.
...
...
..
1050.........1060.

...


..
...1070.....
.
..
.1080....
.....
1090.
.......
.
1100
.......

..1110..
.
......
1120..
.....
..1130
.
......
..1140
.
.

..
..
...1150......
...
1160
.....
....1170.

.
......
.1180..
.
.
....

.1190.....

..
..1200.........1210.....
.
.

..1220.....
....
1230...
...
.
.

.1240...
......1250
.



.....

...1260.....
.
...
1270.

.
.......1280.
........
1290.

.
......

.
1300.


..
.
.....
1310.

.

.......1320.....

.
...1330.
..

......1340....
...
..1350
.
.
.......1360
.

........1370....
.
.

.
..1380..
.....
..1390

....
.....1400......
.

..
1410.
.......

.
1420
.

.
.

......1430..
.
.....

.
1440.
.
.....
..1450.
.
.....
..
1460..

..
....
.1470....
....
.

1480.........1490.........1500...
.
.....
1510......

...1520.....
...


.

1530
.....

....1540.
.
.

.
..

..
.1550
....

.
....

1560
.........1570......

...
1580
.
.

..

.
.
..
.1590....
.
....1600.....

.
..

.
1610
...
.
.....1620.

.
......

.1630...
......1640.

..
..

.
.

.
.
1650
.
.
.......1660.
.
.
.

.
.

.

.
.1670.........1680.

.
.
.

.....
1690.
..
...
.
..1700...
....
.

.1710.......
..1720.
.....
..


.

1730
.........1740.........1750.....
.
.
..1760
.........1770....
.
....1780..
.

.
.....1790.........1800..
.
...
.
..1810.........1820.
........1830....
.
.

..
.
1840.........
1850
.
.
.
.
.....1860.........1870
.

.
.......1880.....
.
.

..
1890.........1900....
.
.
..

.
1910
.
........1920........
.1930.....
....1940.........1950.........1960.........1970.........1980.........1990.........2000 Simulation finished.
